In [2]:
import os
import cv2
import numpy as np
from ultralytics import YOLO
from torchvision import models, transforms
from sklearn.cluster import KMeans
import torch
from matplotlib import pyplot as plt
from PIL import Image

In [3]:
model = YOLO("yolov8n.pt").to('cuda')

In [4]:
print(model.device)

cuda:0


In [5]:
# Define Paths
images_folder = 'dataset/cats'  # Replace with your image folder path
output_folder = 'output/'  # Folder to save cropped cat images
os.makedirs(output_folder, exist_ok=True)

In [6]:
# Function to save bounding boxes in YOLO format
def save_yolo_format(bounding_boxes, filename, image_width, image_height):
    with open(filename, 'w') as f:
        for box in bounding_boxes:
            class_id = box['class_id']
            # Normalize the bounding box coordinates
            x_min = box['x_min']
            y_min = box['y_min']
            x_max = box['x_max']
            y_max = box['y_max']
            
            # Center and size of the bounding box
            x_center = (x_min + x_max) / 2.0 / image_width
            y_center = (y_min + y_max) / 2.0 / image_height
            width = (x_max - x_min) / float(image_width)
            height = (y_max - y_min) / float(image_height)

            # Write in YOLO format: class_id x_center y_center width height
            f.write(f"{class_id} {x_center} {y_center} {width} {height}\n")

In [ ]:
# Iterate through images in the dataset folder
for image_name in os.listdir(images_folder):
    image_path = os.path.join(images_folder, image_name)
    image = cv2.imread(image_path)

    # Run YOLO inference
    results = model.predict(source=image_path, save=True)

    # Prepare a list to collect bounding box data for YOLO format
    bounding_boxes = []

    # Get the image dimensions for normalization
    image_height, image_width, _ = image.shape

    # Iterate over the results to get bounding boxes
    for result in results:
        boxes = result.boxes  # List of detected boxes

        for box in boxes:
            # Get coordinates, class id, and confidence score
            x_min, y_min, x_max, y_max = map(int, box.xyxy[0])  # Bounding box coordinates
            class_id = int(box.cls[0])  # Class id

            # Store the bounding box details
            bounding_boxes.append({
                "class_id": class_id,
                "x_min": x_min,
                "y_min": y_min,
                "x_max": x_max,
                "y_max": y_max
            })

    # Save the bounding boxes to a YOLO format .txt file
    yolo_txt_filename = os.path.join(output_folder, f"{image_name.split('.')[0]}.txt")
    save_yolo_format(bounding_boxes, yolo_txt_filename, image_width, image_height)

    # Optionally: Draw bounding boxes on the image (to save as visual feedback)
    for box in bounding_boxes:
        x_min, y_min, x_max, y_max = box["x_min"], box["y_min"], box["x_max"], box["y_max"]
        cv2.rectangle(image, (x_min, y_min), (x_max, y_max), (0, 255, 0), 2)

print(f"Processed all images. YOLO format bounding boxes saved to {output_folder}")


image 1/1 e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\1818949000-IMG-20240118-WA0001.jpg: 640x384 1 cat, 1 chair, 34.0ms
Speed: 5.0ms preprocess, 34.0ms inference, 6.0ms postprocess per image at shape (1, 3, 640, 384)
Results saved to runs\detect\predict2

image 1/1 e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_103335.jpg: 640x480 1 cat, 1 bear, 2 chairs, 147.3ms
Speed: 7.0ms preprocess, 147.3ms inference, 3.0ms postprocess per image at shape (1, 3, 640, 480)
Results saved to runs\detect\predict2

image 1/1 e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_141622.jpg: 640x480 1 person, 2 cats, 61.6ms
Speed: 7.0ms preprocess, 61.6ms inference, 4.4ms postprocess per image at shape (1, 3, 640, 480)
Results saved to runs\detect\predict2

image 1/1 e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_184600.jpg: 640x480 1 person, 1 cat, 1 remote, 1 book, 1 teddy bear, 70.0ms
Speed: 8.0ms preprocess, 70.0ms inference, 5.0ms postprocess per image at shap

In [11]:
results = model.predict(source=images_folder, save=False)


image 1/558 e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\1818949000-IMG-20240118-WA0001.jpg: 640x384 1 cat, 1 chair, 28.4ms
image 2/558 e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_103335.jpg: 640x480 1 cat, 1 bear, 2 chairs, 84.9ms
image 3/558 e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_141622.jpg: 640x480 1 person, 2 cats, 145.9ms
image 4/558 e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_184600.jpg: 640x480 1 person, 1 cat, 1 remote, 1 book, 1 teddy bear, 77.2ms
image 5/558 e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_195833.jpg: 640x480 1 cat, 1 bed, 56.5ms
image 6/558 e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_200052.jpg: 640x480 1 person, 1 cat, 68.0ms
image 7/558 e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_200057.jpg: 640x480 1 cat, 1 bed, 48.0ms
image 8/558 e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_200102.jpg: 640x480 1 person, 1 cat, 1 bed, 41.0ms
image 9/558 e:

In [ ]:
os.makedirs(output_folder+'cropped', exist_ok=True)  # Ensure the directory exists
cat_count = 0  # Counter for saving cat images
for result in results:
    boxes = result.boxes

    for box in boxes:
        # Get class ID and confidence
        class_id = int(box.cls[0])
        confidence = box.conf[0]

        # Process only "cat" items (cls id = 15)
        if class_id == 15:
            # Get bounding box coordinates
            x_min, y_min, x_max, y_max = map(int, box.xyxy[0])

            # Crop the image
            cropped_cat = result.orig_img[y_min:y_max, x_min:x_max]

            # Save the cropped image
            cat_count += 1
            output_path = os.path.join(output_folder,f"cropped/cat_{result}.jpg")
            cv2.imwrite(output_path, cropped_cat)

            print(f"Saved cropped cat image: {output_path}")

Saved cropped cat image: output/cropped/cat_1.jpg
Saved cropped cat image: output/cropped/cat_2.jpg
Saved cropped cat image: output/cropped/cat_3.jpg
Saved cropped cat image: output/cropped/cat_4.jpg
Saved cropped cat image: output/cropped/cat_5.jpg
Saved cropped cat image: output/cropped/cat_6.jpg
Saved cropped cat image: output/cropped/cat_7.jpg
Saved cropped cat image: output/cropped/cat_8.jpg
Saved cropped cat image: output/cropped/cat_9.jpg
Saved cropped cat image: output/cropped/cat_10.jpg
Saved cropped cat image: output/cropped/cat_11.jpg
Saved cropped cat image: output/cropped/cat_12.jpg
Saved cropped cat image: output/cropped/cat_13.jpg
Saved cropped cat image: output/cropped/cat_14.jpg
Saved cropped cat image: output/cropped/cat_15.jpg
Saved cropped cat image: output/cropped/cat_16.jpg
Saved cropped cat image: output/cropped/cat_17.jpg
Saved cropped cat image: output/cropped/cat_18.jpg
Saved cropped cat image: output/cropped/cat_19.jpg
Saved cropped cat image: output/cropped/

In [27]:
# Feature Extraction with ResNet18
# Load ResNet18 Model
resnet = models.resnet18(pretrained=True)
resnet = torch.nn.Sequential(*(list(resnet.children())[:-1]))  # Remove classification layer
resnet.eval()

# Define Preprocessing
preprocess = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])


c:\Users\danie\AppData\Local\Programs\Python\Python310\lib\site-packages\torchvision\models\_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
c:\Users\danie\AppData\Local\Programs\Python\Python310\lib\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet18_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet18_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


In [28]:
# Extract Features
def extract_features(image_path):
    img = Image.open(image_path).convert("RGB")
    img_tensor = preprocess(img).unsqueeze(0)
    with torch.no_grad():
        features = resnet(img_tensor)
    return features.squeeze().numpy()

In [34]:
crop_folder = 'output/cropped'
feature_list = []
crop_images = [os.path.join(crop_folder, img) for img in os.listdir(crop_folder) if img.endswith(".jpg")]

In [43]:
for crop_path in crop_images:
    features = extract_features(crop_path)
    feature_list.append(features)

In [44]:
# Convert the list of features into a NumPy array
features_array = np.array(feature_list)
# Perform K-Means clustering (2 clusters for your case)
kmeans = KMeans(n_clusters=2, random_state=42)
labels = kmeans.fit_predict(features_array)

In [45]:
# Print which image belongs to which cluster
for i, crop_path in enumerate(crop_images):
    cluster = labels[i]
    print(f"{os.path.basename(crop_path)} belongs to cluster {cluster}")

cat_1.jpg belongs to cluster 0
cat_10.jpg belongs to cluster 0
cat_100.jpg belongs to cluster 0
cat_101.jpg belongs to cluster 1
cat_102.jpg belongs to cluster 0
cat_103.jpg belongs to cluster 0
cat_104.jpg belongs to cluster 0
cat_105.jpg belongs to cluster 0
cat_106.jpg belongs to cluster 1
cat_107.jpg belongs to cluster 1
cat_108.jpg belongs to cluster 0
cat_109.jpg belongs to cluster 1
cat_11.jpg belongs to cluster 0
cat_110.jpg belongs to cluster 1
cat_111.jpg belongs to cluster 1
cat_112.jpg belongs to cluster 1
cat_113.jpg belongs to cluster 1
cat_114.jpg belongs to cluster 1
cat_115.jpg belongs to cluster 1
cat_116.jpg belongs to cluster 1
cat_117.jpg belongs to cluster 1
cat_118.jpg belongs to cluster 1
cat_119.jpg belongs to cluster 1
cat_12.jpg belongs to cluster 0
cat_120.jpg belongs to cluster 1
cat_121.jpg belongs to cluster 1
cat_122.jpg belongs to cluster 1
cat_123.jpg belongs to cluster 0
cat_124.jpg belongs to cluster 0
cat_125.jpg belongs to cluster 0
cat_126.jpg bel

In [54]:
labels_folder = 'dataset/annotations'   # Path to save YOLO annotation files
os.makedirs(labels_folder, exist_ok=True)

In [53]:
def save_yolo_annotations(cropped_image_path, label, box, labels_folder):
    """
    Save YOLO annotation for the given image.
    :param cropped_image_path: Path to the cropped image
    :param label: Cluster label (0 or 1)
    :param box: The bounding box (x1, y1, x2, y2) coordinates
    :param labels_folder: Folder to save the annotations
    """
    # Extract image name without extension
    image_name = os.path.basename(cropped_image_path).split('.')[0]
    
    # Normalize the bounding box coordinates
    image = cv2.imread(cropped_image_path)
    h, w, _ = image.shape

    # YOLO requires normalized coordinates: (x_center, y_center, width, height)
    x_min, y_min, x_max, y_max = box
    x_center = (x_min + x_max) / 2 / w
    y_center = (y_min + y_max) / 2 / h
    width = (x_max - x_min) / w
    height = (y_max - y_min) / h

    # Create the annotation file path
    annotation_path = os.path.join(labels_folder, f"{image_name}.txt")
    
    # Write the YOLO format annotation
    with open(annotation_path, 'w') as f:
        # Write the class id and the normalized bounding box info
        f.write(f"{label} {x_center} {y_center} {width} {height}\n")
    
    print(f"Saved annotation for {image_name}: {annotation_path}")

In [56]:
cropped_data = []  # List to store cropped image data

for result in results:
    boxes = result.boxes
    img_path = result.path
    img = cv2.imread(img_path)

    for i, box in enumerate(boxes):
        class_id = int(box.cls[0])
        if class_id == 15:  # Process only cats (class ID = 15 in COCO dataset)
            x_min, y_min, x_max, y_max = map(int, box.xyxy[0])

            # Crop and save the image
            cropped_cat = img[y_min:y_max, x_min:x_max]
            crop_path = os.path.join(output_folder, f"{os.path.basename(img_path).split('.')[0]}_crop{i}.jpg")
            cv2.imwrite(crop_path, cropped_cat)

            # Store metadata for this crop
            cropped_data.append({
                "cropped_image": crop_path,
                "original_image": img_path,
                "bounding_box": (x_min, y_min, x_max, y_max),
                "box_index": i,  # Index of the box in the original image
            })

In [63]:
feature_list = []
for data in cropped_data:
    features = extract_features(data["cropped_image"])
    feature_list.append(features)

In [64]:
print(len(cropped_data))
print(len(feature_list))

552
552


In [65]:
# Step 5: Clustering with K-Means
# Perform K-Means clustering on the extracted features
features_array = np.array(feature_list)
kmeans = KMeans(n_clusters=2, random_state=42)  # 2 clusters for 2 cats
labels = kmeans.fit_predict(features_array)

# Add cluster labels to `cropped_data`
for i, label in enumerate(labels):
    cropped_data[i]["cluster_label"] = label 

In [66]:
# Step 6: Generate YOLO Annotations
# Group bounding boxes by original image and write YOLO format annotations
annotations = {}

for data in cropped_data:
    original_image = data["original_image"]
    box = data["bounding_box"]
    class_id = data["cluster_label"]  # Use cluster label as YOLO class ID

    # Calculate YOLO format (x_center, y_center, width, height)
    x_min, y_min, x_max, y_max = box
    img = cv2.imread(original_image)
    h, w, _ = img.shape

    x_center = (x_min + x_max) / (2 * w)
    y_center = (y_min + y_max) / (2 * h)
    width = (x_max - x_min) / w
    height = (y_max - y_min) / h

    # Add to annotations
    if original_image not in annotations:
        annotations[original_image] = []
    annotations[original_image].append((class_id, x_center, y_center, width, height))

In [67]:
annotations_folder = 'dataset/annotations/' 
# Save YOLO annotations to files
for original_image, boxes in annotations.items():
    annotation_file = os.path.join(annotations_folder, f"{os.path.basename(original_image).split('.')[0]}.txt")
    with open(annotation_file, "w") as f:
        for class_id, x_center, y_center, width, height in boxes:
            f.write(f"{class_id} {x_center} {y_center} {width} {height}\n")
    print(f"Saved YOLO annotation for {original_image} to {annotation_file}")

Saved YOLO annotation for e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\1818949000-IMG-20240118-WA0001.jpg to dataset/annotations/1818949000-IMG-20240118-WA0001.txt
Saved YOLO annotation for e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_103335.jpg to dataset/annotations/20240308_103335.txt
Saved YOLO annotation for e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_141622.jpg to dataset/annotations/20240308_141622.txt
Saved YOLO annotation for e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_184600.jpg to dataset/annotations/20240308_184600.txt
Saved YOLO annotation for e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_195833.jpg to dataset/annotations/20240308_195833.txt
Saved YOLO annotation for e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_200052.jpg to dataset/annotations/20240308_200052.txt
Saved YOLO annotation for e:\Facultate\Master\Anul 1\CV\Project\dataset\cats\20240308_200057.jpg to dataset/annotations/20240308_2

In [68]:
import shutil
from sklearn.model_selection import train_test_split

In [70]:
# Define the paths
original_images_path = "dataset/Cats"
original_annotations_path = "dataset/annotations"

# Define the YOLO structure paths
output_images_train = "dataset/images/train"
output_images_val = "dataset/images/val"
output_labels_train = "dataset/labels/train"
output_labels_val = "dataset/labels/val"

# Create YOLO directory structure
os.makedirs(output_images_train, exist_ok=True)
os.makedirs(output_images_val, exist_ok=True)
os.makedirs(output_labels_train, exist_ok=True)
os.makedirs(output_labels_val, exist_ok=True)

In [83]:
# Get all image and annotation files
images = {os.path.splitext(f)[0]: f for f in os.listdir(original_images_path)}
annotations = {os.path.splitext(f)[0]: f for f in os.listdir(original_annotations_path) if f.endswith(".txt")}

# Match images to their annotations (by base name)
matched_files = [(images[key], annotations[key]) for key in images if key in annotations]

if not matched_files:
    raise ValueError("No matching images and annotations found!")

In [87]:
print(len(images))
print(len(annotations))
print(len(matched_files))

558
465
465


In [86]:
# Split into train and validation sets
train_files, val_files = train_test_split(matched_files, test_size=0.2, random_state=42)

In [88]:
# Function to copy files
def copy_files(file_pairs, src_image_folder, src_label_folder, dest_image_folder, dest_label_folder):
    for img_file, ann_file in file_pairs:
        # Copy image
        shutil.copy(os.path.join(src_image_folder, img_file), os.path.join(dest_image_folder, img_file))
        # Copy annotation
        shutil.copy(os.path.join(src_label_folder, ann_file), os.path.join(dest_label_folder, ann_file))

# Copy training files
copy_files(train_files, original_images_path, original_annotations_path, output_images_train, output_labels_train)

# Copy validation files
copy_files(val_files, original_images_path, original_annotations_path, output_images_val, output_labels_val)


In [89]:
model.train(
    data="cats_dataset.yaml",  # Path to the dataset YAML file
    epochs=50,            # Number of training epochs
    imgsz=640,            # Image size (default is 640x640)
    batch=16,             # Batch size (adjust based on your GPU memory)
    name="cat_detection", # Name of the training run
    workers=4             # Number of data-loading workers (adjust as needed)
)

engine\trainer: task=detect, mode=train, model=yolov8n.pt, data=cats_dataset.yaml, epochs=50, time=None, patience=100, batch=16, imgsz=640, save=True, save_period=-1, cache=False, device=cuda:0, workers=4, project=None, name=cat_detection, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=False, save_frames=False, save_txt=False, save_conf=False, save_crop=False, show_labels=True, show_conf=True, show_boxes=True, line_width=None, format=torchscript, keras=False, optimize=False, int8=Fal

100%|██████████| 755k/755k [00:00<00:00, 4.81MB/s]


Overriding model.yaml nc=80 with nc=2

                   from  n    params  module                                       arguments                     
  0                  -1  1       464  ultralytics.nn.modules.conv.Conv             [3, 16, 3, 2]                 
  1                  -1  1      4672  ultralytics.nn.modules.conv.Conv             [16, 32, 3, 2]                
  2                  -1  1      7360  ultralytics.nn.modules.block.C2f             [32, 32, 1, True]             
  3                  -1  1     18560  ultralytics.nn.modules.conv.Conv             [32, 64, 3, 2]                
  4                  -1  2     49664  ultralytics.nn.modules.block.C2f             [64, 64, 2, True]             
  5                  -1  1     73984  ultralytics.nn.modules.conv.Conv             [64, 128, 3, 2]               
  6                  -1  2    197632  ultralytics.nn.modules.block.C2f             [128, 128, 2, True]           
  7                  -1  1    295424  ultralytics

100%|██████████| 5.35M/5.35M [00:00<00:00, 10.1MB/s]


AMP: checks passed 


...

                   all         93        115      0.943      0.897      0.951      0.802



50 epochs completed in 0.383 hours.
Optimizer stripped from runs\detect\cat_detection\weights\last.pt, 6.2MB
Optimizer stripped from runs\detect\cat_detection\weights\best.pt, 6.2MB

Validating runs\detect\cat_detection\weights\best.pt...
Ultralytics 8.3.65  Python-3.10.9 torch-2.5.1+cu124 CUDA:0 (NVIDIA GeForce RTX 4060 Ti, 8187MiB)
Model summary (fused): 168 layers, 3,006,038 parameters, 0 gradients, 8.1 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 3/3 [00:01<00:00,  1.61it/s]


                   all         93        115      0.943      0.897      0.951      0.804
                   Tom         56         64      0.965      0.853      0.935      0.801
              Garfield         48         51      0.922      0.941      0.966      0.806
Speed: 2.1ms preprocess, 1.8ms inference, 0.0ms loss, 2.5ms postprocess per image
Results saved to runs\detect\cat_detection


ultralytics.utils.metrics.DetMetrics object with attributes:

ap_class_index: array([0, 1])
box: ultralytics.utils.metrics.Metric object
confusion_matrix: <ultralytics.utils.metrics.ConfusionMatrix object at 0x00000219175CD420>
curves: ['Precision-Recall(B)', 'F1-Confidence(B)', 'Precision-Confidence(B)', 'Recall-Confidence(B)']
curves_results: [[array([          0,    0.001001,    0.002002,    0.003003,    0.004004,    0.005005,    0.006006,    0.007007,    0.008008,    0.009009,     0.01001,    0.011011,    0.012012,    0.013013,    0.014014,    0.015015,    0.016016,    0.017017,    0.018018,    0.019019,     0.02002,    0.021021,    0.022022,    0.023023,
          0.024024,    0.025025,    0.026026,    0.027027,    0.028028,    0.029029,     0.03003,    0.031031,    0.032032,    0.033033,    0.034034,    0.035035,    0.036036,    0.037037,    0.038038,    0.039039,     0.04004,    0.041041,    0.042042,    0.043043,    0.044044,    0.045045,    0.046046,    0.047047,
          0.0

In [95]:
model = YOLO("runs/detect/cat_detection/weights/best.pt")
# Validate on the validation dataset
metrics = model.val(data="cats_dataset.yaml")
print(metrics)

Ultralytics 8.3.65  Python-3.10.9 torch-2.5.1+cu124 CUDA:0 (NVIDIA GeForce RTX 4060 Ti, 8187MiB)
Model summary (fused): 168 layers, 3,006,038 parameters, 0 gradients, 8.1 GFLOPs


val: Scanning E:\Facultate\Master\Anul 1\CV\Project\dataset\labels\val.cache... 93 images, 0 backgrounds, 0 corrupt: 100%|██████████| 93/93 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 6/6 [00:17<00:00,  2.85s/it]


                   all         93        115      0.943      0.898      0.948      0.798
                   Tom         56         64      0.965      0.854      0.932      0.789
              Garfield         48         51      0.921      0.941      0.965      0.806
Speed: 1.7ms preprocess, 4.4ms inference, 0.0ms loss, 3.1ms postprocess per image
Results saved to runs\detect\val
ultralytics.utils.metrics.DetMetrics object with attributes:

ap_class_index: array([0, 1])
box: ultralytics.utils.metrics.Metric object
confusion_matrix: <ultralytics.utils.metrics.ConfusionMatrix object at 0x00000218AEB70400>
curves: ['Precision-Recall(B)', 'F1-Confidence(B)', 'Precision-Confidence(B)', 'Recall-Confidence(B)']
curves_results: [[array([          0,    0.001001,    0.002002,    0.003003,    0.004004,    0.005005,    0.006006,    0.007007,    0.008008,    0.009009,     0.01001,    0.011011,    0.012012,    0.013013,    0.014014,    0.015015,    0.016016,    0.017017,    0.018018,    0.019019,   

In [99]:
results = model.predict(source="dataset/Cats/20250122_142949.jpg", save=True, conf=0.5)

# View the results
for result in results:
    print(result)


image 1/1 e:\Facultate\Master\Anul 1\CV\Project\dataset\Cats\20250122_142949.jpg: 640x480 1 Tom, 1 Garfield, 25.0ms
Speed: 4.0ms preprocess, 25.0ms inference, 6.0ms postprocess per image at shape (1, 3, 640, 480)
Results saved to runs\detect\predict3
ultralytics.engine.results.Results object with attributes:

boxes: ultralytics.engine.results.Boxes object
keypoints: None
masks: None
names: {0: 'Tom', 1: 'Garfield'}
obb: None
orig_img: array([[[ 64,  50,  38],
        [ 67,  53,  41],
        [ 69,  55,  43],
        ...,
        [ 90, 122, 133],
        [ 87, 119, 130],
        [ 85, 117, 128]],

       [[ 63,  49,  37],
        [ 66,  52,  40],
        [ 70,  56,  44],
        ...,
        [ 70, 102, 113],
        [ 67,  99, 110],
        [ 72, 104, 115]],

       [[ 66,  52,  40],
        [ 67,  53,  41],
        [ 71,  57,  45],
        ...,
        [ 53,  85,  96],
        [ 51,  83,  94],
        [ 58,  90, 101]],

       ...,

       [[144, 146, 146],
        [147, 149, 149],
  

In [118]:
input_video_path = 'dataset/20250123_090113.mp4'  # Replace with your video file path
cap = cv2.VideoCapture(input_video_path)

In [119]:
# Get the video frame rate and size
fps = int(cap.get(cv2.CAP_PROP_FPS))  # Frame per second
frame_width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
frame_height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))

In [120]:
# Define the codec and output video format
fourcc = cv2.VideoWriter_fourcc(*'XVID')
output_video_path = 'output_video.mp4'  # Path to save the output video
out = cv2.VideoWriter(output_video_path, fourcc, fps, (frame_width, frame_height))

In [121]:
while True:
    ret, frame = cap.read()
    if not ret:
        break  # End of video

    # Perform inference on the frame
    results = model(frame)  # Perform detection on the current frame

    # Draw bounding boxes and labels on the frame
    for result in results:
        boxes = result.boxes
        for box in boxes:
            x1, y1, x2, y2 = map(int, box.xyxy[0])  # Extract bounding box coordinates
            confidence = box.conf[0]  # Confidence score

            # Draw the bounding box
            class_id = int(box.cls[0])
            cv2.rectangle(frame, (x1, y1), (x2, y2), (0, 255, 0), 2)
            label = f"{result.names[class_id]} ({confidence:.2f})"
            # Put the label text
            cv2.putText(frame, label, (x1, y1-10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)

    # Write the frame with bounding boxes to the output video
    out.write(frame)

# Release the video objects
cap.release()
out.release()

print("Video processing completed and saved as 'output_video.mp4'")


0: 640x384 (no detections), 75.8ms
Speed: 6.3ms preprocess, 75.8ms inference, 2.7ms postprocess per image at shape (1, 3, 640, 384)

0: 640x384 (no detections), 84.7ms
Speed: 11.0ms preprocess, 84.7ms inference, 3.0ms postprocess per image at shape (1, 3, 640, 384)

0: 640x384 (no detections), 11.1ms
Speed: 3.9ms preprocess, 11.1ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 384)

0: 640x384 (no detections), 10.5ms
Speed: 3.0ms preprocess, 10.5ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 384)

0: 640x384 (no detections), 10.0ms
Speed: 3.0ms preprocess, 10.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 384)

0: 640x384 (no detections), 10.2ms
Speed: 3.0ms preprocess, 10.2ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 384)

0: 640x384 (no detections), 10.0ms
Speed: 3.0ms preprocess, 10.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 384)

0: 640x384 (no detections), 10.0ms
Speed: 3.0ms preprocess, 10.0ms 

In [122]:
for result in results:
    print(result.names)
    break

{0: 'Tom', 1: 'Garfield'}
